In [57]:
import pandas as pd
import os
import seaborn as sns
import matplotlib.pyplot as plt
from folium.plugins import HeatMap
import folium
import plotly.express as px
import pydeck as pdk
import streamlit as st

##### Join two datasets and have pickup and drop off details with lat/lon

In [58]:
table1 = pd.read_excel(r"C:\Projects\VGI Challenge\vgi_hackathon_2024\FLEXI_bus_stops.xls")
table2 = pd.read_excel(r"C:\Projects\VGI Challenge\vgi_hackathon_2024\FLEXI_trip_data.xls")

merged_data = table2.merge(table1, left_on="Pickup ID", right_on="index") \
                    .merge(table1, left_on="Dropoff ID", right_on="index", suffixes=('', '_dropoff')) \
                    .rename(columns={
                        "index": "pickup_index",
                        "name": "pickup_name",
                        "district": "pickup_district",
                        "latitude": "pickup_latitude",
                        "longitude": "pickup_longitude"
                    }) \
                    .drop(columns=["Pickup ID", "Dropoff ID"])


In [59]:
table2.info()
merged_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3838 entries, 0 to 3837
Data columns (total 8 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Booking ID           3838 non-null   int64         
 1   Status               3838 non-null   object        
 2   Passenger status     3838 non-null   object        
 3   Passengers           3838 non-null   int64         
 4   Pickup ID            3838 non-null   int64         
 5   Dropoff ID           3838 non-null   int64         
 6   Actual Pickup Time   3838 non-null   datetime64[ns]
 7   Actual Dropoff Time  3838 non-null   datetime64[ns]
dtypes: datetime64[ns](2), int64(4), object(2)
memory usage: 240.0+ KB
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3434 entries, 0 to 3433
Data columns (total 16 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   Booking ID           3434 n

In [60]:
merged_data['Actual Pickup Time'] = pd.to_datetime(merged_data['Actual Pickup Time'])
merged_data['Actual Dropoff Time'] = pd.to_datetime(merged_data['Actual Dropoff Time'])
merged_data['Pickup Hour'] = merged_data['Actual Pickup Time'].dt.hour
merged_data['Pickup Day'] = merged_data['Actual Pickup Time'].dt.dayofweek  # 0 = Monday, 1= Tuesday, 2 = Wednesday ... 

In [61]:
merged_data.head()

Booking ID               Status Passenger status  Passengers  \
0      253212  Cancelled by client        Cancelled           1   
1      253369  Cancelled by client        Cancelled           3   
2      253808  Cancelled by driver        Cancelled           2   
3      253782            Validated   Trip completed           2   
4      252382  Cancelled by driver        Cancelled           1   

   Actual Pickup Time Actual Dropoff Time  pickup_index  \
0 2024-09-01 08:18:00 2024-09-01 08:34:00            40   
1 2024-09-01 08:46:00 2024-09-01 09:09:00            66   
2 2024-09-01 08:56:00 2024-09-01 09:09:00            30   
3 2024-09-01 09:14:00 2024-09-01 09:25:00            40   
4 2024-09-01 09:41:00 2024-09-01 09:49:00            46   

                 pickup_name pickup_district  pickup_latitude  \
0  Irfersdorf, Am Kirchplatz      Irfersdorf        48.994215   
1        Wiesenhofen, Kirche    Litterzhofen        49.043035   
2   Beilngries, Frauenkirche      Beilngries        49.036378   
3  Irfersdorf, Am Kirchplatz      Irfersdorf        48.994215   
4     Aschbuch, Waldsiedlung        Aschbuch        48.976207   

   pickup_longitude  index_dropoff                   name_dropoff  \
0         11.461103              0               Kinding, Bahnhof   
1         11.412738              0               Kinding, Bahnhof   
2         11.470632              0               Kinding, Bahnhof   
3         11.461103             21      Beilngries, Deutscher Hof   
4         11.491877             22  Beilngries, Kelheimer Stra√üe   

  district_dropoff  latitude_dropoff  longitude_dropoff  Pickup Hour  \
0          Kinding         48.992168          11.377365            8   
1          Kinding         48.992168          11.377365            8   
2          Kinding         48.992168          11.377365            8   
3       Beilngries         49.033525          11.475793            9   
4       Beilngries         49.032928          11.479163            9   

   Pickup Day  
0           6  
1           6  
2           6  
3           6  
4           6

In [62]:
#Find most common drop off for each pickup location

pickup_demand_counts = (
                        merged_data.groupby(['pickup_index']) \
                        .size() \
                        .reset_index(name = "count"))

# most_common_dropoff = pickup_dropoff_counts.loc[
#             pickup_dropoff_counts.groupby('pickup_index')['count'].idxmax()
# ]

pickup_demand_counts

pickup_index  count
0              0    680
1              1     72
2              2     20
3              3     29
4              4     70
..           ...    ...
59            64     73
60            65      6
61            66     22
62            67     29
63            68      2

[64 rows x 2 columns]

In [63]:
#Number of passengers for each passenger

passenger_count_by_status = merged_data.groupby('Status')['Passengers'].sum().reset_index()

passenger_count_by_status

Status  Passengers
0  Cancelled by call center           5
1       Cancelled by client        1320
2       Cancelled by driver         541
3          Changed by admin           8
4         Changed by client           5
5                 Validated        2473

In [64]:
#Number of passenger for each day and each hour

passenger_count_by_day_hour_pickup = (
    merged_data.groupby(['Pickup Day', 'Pickup Hour', 'pickup_index'])['Passengers']
    .sum()
    .reset_index()
)

passenger_count_by_day_hour_pickup.sort_values(by='Passengers', ascending=False)

Pickup Day  Pickup Hour  pickup_index  Passengers
1362           5           20             0          35
183            0           16             0          29
1370           5           21             0          27
146            0           14             0          26
1159           4           20             0          25
...          ...          ...           ...         ...
710            3            6            53           1
712            3            6            59           1
714            3            7             3           1
716            3            7             8           1
1523           6           20            30           1

[1524 rows x 4 columns]

In [65]:
# Group by Pickup Demand
pickup_demand = merged_data.groupby(['pickup_name', 'pickup_latitude', 'pickup_longitude'])['Passengers'].sum().reset_index(name='demand')

# Interactive map heatmap
map_center = [pickup_demand['pickup_latitude'].mean(), pickup_demand['pickup_longitude'].mean()]
map_ = folium.Map(location=map_center, zoom_start=10)
HeatMap(data=pickup_demand[['pickup_latitude', 'pickup_longitude', 'demand']].values, radius=15).add_to(map_)
map_.save("pickup_demand_heatmap.html")

In [66]:
#hourly demand
hourly_demand = merged_data.groupby('Pickup Hour').size().reset_index(name='demand')

hourly_demand

Pickup Hour  demand
0             5     117
1             6     166
2             7     179
3             8     207
4             9     145
5            10     143
6            11     186
7            12     195
8            13     219
9            14     323
10           15     297
11           16     326
12           17     247
13           18     177
14           19     164
15           20     181
16           21     121
17           22      41

In [67]:
merged_data

Booking ID               Status Passenger status  Passengers  \
0         253212  Cancelled by client        Cancelled           1   
1         253369  Cancelled by client        Cancelled           3   
2         253808  Cancelled by driver        Cancelled           2   
3         253782            Validated   Trip completed           2   
4         252382  Cancelled by driver        Cancelled           1   
...          ...                  ...              ...         ...   
3429      270319  Cancelled by driver        Cancelled           3   
3430      268219            Validated   Trip completed           1   
3431      269630  Cancelled by client        Cancelled           1   
3432      269524  Cancelled by client        Cancelled           1   
3433      269863            Validated   Trip completed           1   

      Actual Pickup Time Actual Dropoff Time  pickup_index  \
0    2024-09-01 08:18:00 2024-09-01 08:34:00            40   
1    2024-09-01 08:46:00 2024-09-01 09:09:00            66   
2    2024-09-01 08:56:00 2024-09-01 09:09:00            30   
3    2024-09-01 09:14:00 2024-09-01 09:25:00            40   
4    2024-09-01 09:41:00 2024-09-01 09:49:00            46   
...                  ...                 ...           ...   
3429 2024-09-30 20:55:00 2024-09-30 21:42:00             0   
3430 2024-09-30 21:20:00 2024-09-30 21:23:00             4   
3431 2024-09-30 21:25:00 2024-09-30 21:33:00             2   
3432 2024-09-30 21:37:00 2024-09-30 21:47:00            19   
3433 2024-09-30 21:46:00 2024-09-30 21:52:00            33   

                    pickup_name pickup_district  pickup_latitude  \
0     Irfersdorf, Am Kirchplatz      Irfersdorf        48.994215   
1           Wiesenhofen, Kirche    Litterzhofen        49.043035   
2      Beilngries, Frauenkirche      Beilngries        49.036378   
3     Irfersdorf, Am Kirchplatz      Irfersdorf        48.994215   
4        Aschbuch, Waldsiedlung        Aschbuch        48.976207   
...                         ...             ...              ...   
3429           Kinding, Bahnhof         Kinding        48.992168   
3430        Kinding, Marktplatz         Kinding        49.000562   
3431    Enkering, Feuerwehrhaus        Enkering        48.993652   
3432    Beilngries, Ringstrasse      Beilngries        49.033832   
3433  Beilngries, Bauhofstra√üe      Beilngries        49.031608   

      pickup_longitude  index_dropoff                       name_dropoff  \
0            11.461103              0                   Kinding, Bahnhof   
1            11.412738              0                   Kinding, Bahnhof   
2            11.470632              0                   Kinding, Bahnhof   
3            11.461103             21          Beilngries, Deutscher Hof   
4            11.491877             22      Beilngries, Kelheimer Stra√üe   
...                ...            ...                                ...   
3429         11.377365             64  Plankstetten, Biberbacher Stra√üe   
3430         11.382790              1                  Enkering, Maibaum   
3431         11.361228             10              Pfraundorf, Dorfplatz   
3432         11.471982             42          Grampersdorf, Landstrasse   
3433         11.461872             15            Hirschberg, Dorfkapelle   

     district_dropoff  latitude_dropoff  longitude_dropoff  Pickup Hour  \
0             Kinding         48.992168          11.377365            8   
1             Kinding         48.992168          11.377365            8   
2             Kinding         48.992168          11.377365            8   
3          Beilngries         49.033525          11.475793            9   
4          Beilngries         49.032928          11.479163            9   
...               ...               ...                ...          ...   
3429        Biberbach         49.068532          11.455142           20   
3430         Enkering         48.992498          11.363953           21   
3431       Pfra

In [68]:
map_center = [merged_data['pickup_latitude'].mean(), merged_data['pickup_longitude'].mean()]

hex_layer = pdk.Layer(
    "HexagonLayer",
    data=merged_data,
    get_position=["pickup_longitude", "pickup_latitude"],
    radius=150, 
    elevation_scale=30,  
    elevation_range=[0, 100],  
    extruded=True,
    pickable=True,
    coverage=0.5,  
)

view_state = pdk.ViewState(
    latitude=map_center[0],
    longitude=map_center[1],
    zoom=10,
    pitch=45  # angle to tilt the view
)

deck_map = pdk.Deck(
    layers=[hex_layer],
    initial_view_state=view_state,
    #map_style="mapbox://styles/mapbox/light-v9",
)

deck_map.to_html("3d_pickup_demand_heatmap.html")


In [69]:
map_center = [merged_data['latitude_dropoff'].mean(), merged_data['longitude_dropoff'].mean()]

hex_layer = pdk.Layer(
    "HexagonLayer",
    data=merged_data,
    get_position=["longitude_dropoff", "latitude_dropoff"],
    radius=150, 
    elevation_scale=30,  
    elevation_range=[0, 100],  
    extruded=True,
    pickable=True,
    coverage=0.5,  
)

view_state = pdk.ViewState(
    latitude=map_center[0],
    longitude=map_center[1],
    zoom=10,
    pitch=45  # angle to tilt the view
)

deck_map = pdk.Deck(
    layers=[hex_layer],
    initial_view_state=view_state,
    #map_style="mapbox://styles/mapbox/light-v9",
)

deck_map.to_html("3d_dropoff_demand_heatmap.html")

In [74]:
os.environ["MAPBOX_API_KEY"] = "pk.eyJ1Ijoiam5haXIiLCJhIjoiY20zYTh1bTRrMTdxbTJscjZyd2Jrbjk5aCJ9.4HXOmaBtz_1udpXKAAf9bA"


# Sidebar filters
st.sidebar.header("Filter Options")
min_demand = st.sidebar.slider("Minimum Demand", int(pickup_demand_counts['count'].min()), int(pickup_demand_counts['count'].max()), 0)
filtered_data = pickup_demand_counts[pickup_demand_counts['count'] >= min_demand]

# Define the 3D HexagonLayer
hex_layer = pdk.Layer(
    "HexagonLayer",
    data=merged_data,
    get_position=["pickup_longitude", "pickup_latitude"],
    radius=200,
    elevation_scale=50,
    elevation_range=[0, 100],
    extruded=True,
    coverage=1,
)

# Define the view settings for the map
view_state = pdk.ViewState(
    latitude=merged_data['pickup_latitude'].mean(),
    longitude=merged_data['pickup_longitude'].mean(),
    zoom=10,
    pitch=45,
)

# Create the PyDeck map
deck_map = pdk.Deck(
    layers=[hex_layer],
    initial_view_state=view_state,
    map_style="mapbox://styles/mapbox/light-v9",
    #mapbox_key=os.getenv("MAPBOX_API_KEY")
)

# Display the map in Streamlit
st.title("VGI-Flexi Demand Dashboard")
st.write("### 3D Heatmap of Demand")
st.pydeck_chart(deck_map)

2024-11-10 11:37:33.335 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.336 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.337 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.337 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.338 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.338 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.338 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.
2024-11-10 11:37:33.520 Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bar

DeltaGenerator()